In [1]:
from jupyter_server.services.kernels.kernelmanager import MappingKernelManager

idle_timeout = MappingKernelManager.cull_idle_timeout.default_value
print(f"Idle Kernel Culling Timeout: {idle_timeout} seconds")

Idle Kernel Culling Timeout: 0 seconds


In [2]:
from jupyter_server.serverapp import ServerApp

no_activity_timeout = ServerApp.shutdown_no_activity_timeout.default_value
print(f"Activity Timeout: {no_activity_timeout} seconds")

Activity Timeout: 0 seconds


In [16]:
import numpy as np
import pandas as pd
import geopandas as gpd
import torch
import torch.nn as nn
import torch.optim as optim
from torch.optim.lr_scheduler import CyclicLR
from sklearn.metrics import r2_score
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import train_test_split
import optuna
from optuna.pruners import MedianPruner
import optuna.visualization as vis

In [4]:
df = gpd.read_file('C:/Users/lewil/OneDrive - University of Bristol/Msc Geographic Data Science & Spatial Analytics/Dissertation/combined_df.gpkg')

df.head()

property_id  result_count  num_bathrooms  num_bedrooms  num_recepts  \
0      2485433             2              1             2            1   
1      2482388             1              1             3            2   
2      2483664             2              1             3            1   
3      2488692             2              2             3            2   
4      2473496             3              2             2            1   

   num_floors   price  last_marketed_days  marketed_duration  \
0           0  260000                 328                225   
1           0  350000                 328                  1   
2           0  510000                 342                297   
3           0  475000                 343                274   
4           0  375000                 343                506   

   property_type_Bungalow  ...  status_sale_under_offer  status_sold  IntRate  \
0                     0.0  ...                      0.0          1.0     0.25   
1                     0.0  ...                      0.0          0.0     0.25   
2                     0.0  ...                      0.0          1.0     0.10   
3                     0.0  ...                      0.0          1.0     0.10   
4                     0.0  ...                      0.0          0.0     0.10   

   latitude  longitude   LAD11NM  CouncilTaxEst  POIdensity_score  \
0   51.4301     0.0145  Lewisham        2288.65               6.0   
1   51.4250     0.0142   Bromley        2561.28              11.0   
2   51.4248     0.0240   Bromley        2561.28               0.0   
3   51.4271    -0.0048  Lewisham        2640.75               2.0   
4   51.4091     0.0182   Bromley        2561.28               3.0   

   distance_from_centre                   geometry  
0             72.687308   POINT (0.01450 51.43010)  
1             72.683921   POINT (0.01420 51.42500)  
2             72.676837   POINT (0.02400 51.42480)  
3             72.698864  POINT (-0.00480 51.42710)  
4             72.669866   POINT (0.01820 51.40910)  

[5 rows x 34 columns]

In [5]:
# splitting data into inputs and outputs
X = df.select_dtypes(include=['number']).drop(columns=['price'])
y = df['price']

In [6]:
# checking head and tail
X

property_id  result_count  num_bathrooms  num_bedrooms  num_recepts  \
0           2485433             2              1             2            1   
1           2482388             1              1             3            2   
2           2483664             2              1             3            1   
3           2488692             2              2             3            2   
4           2473496             3              2             2            1   
...             ...           ...            ...           ...          ...   
197631     10288510             3              2             3            3   
197632     10294820             4              1             3            1   
197633     10287769             2              1             2            1   
197634     10290700             8              2             3            3   
197635     10294757             3              1             3            1   

        num_floors  last_marketed_days  marketed_duration  \
0                0                 328                225   
1                0                 328                  1   
2                0                 342                297   
3                0                 343                274   
4                0                 343                506   
...            ...                 ...                ...   
197631           0                7436                  0   
197632           0                7463                  0   
197633           0                7476                  0   
197634           0                7477                  0   
197635           0                7485                  0   

        property_type_Bungalow  property_type_Cottage  ...  \
0                          0.0                    0.0  ...   
1                          0.0                    0.0  ...   
2                          0.0                    0.0  ...   
3                          0.0                    0.0  ...   
4                          0.0                    0.0  ...   
...                        ...                    ...  ...   
197631                     0.0                    0.0  ...   
197632                     0.0                    0.0  ...   
197633                     0.0                    0.0  ...   
197634                     0.0                    0.0  ...   
197635                     0.0                    0.0  ...   

        property_type_other  status_for_sale  status_sale_under_offer  \
0                       0.0              0.0                      0.0   
1                       0.0              1.0                      0.0   
2                       0.0              0.0                      0.0   
3                       0.0              0.0                      0.0   
4                       0.0              1.0                      0.0   
...                     ...              ...                      ...   
197631                  0.0              0.0                      0.0   
197632                  0.0              0.0                      0.0   
197633                  0.0              0.0                      0.0   
197634                  0.0              0.0                      0.0   
197635                  0.0              0.0                      0.0   

        status_sold  IntRate  latitude  longitude  CouncilTaxEst  \
0               1.0     0.25   51.4301     0.0145        2288.65   
1               0.0     0.25   51.4250     0.0142        2561.28   
2               1.0     0.10   51.4248     0.0240        2561.28   
3               1.0     0.10   51.4271    -0.0048        2640.75   
4               0.0     0.10   51.4091     0.0182        2561.28   
...             ...      ...       ...        ...            ...   
197631          1.0     4.00   51.5591    -0.2876        2286.34   
197632          1.0     4.00   51.5694    -0.2817        2638.08   
197633          1.0     4.00   51.5557    -0.2925        1582.85   
197634          1.0     

In [7]:
# converting to tensors
X = torch.tensor(X.values, dtype=torch.float32)
y = torch.tensor(y.values, dtype=torch.float32).reshape(-1, 1)

# checking this has worked
print(isinstance(X, torch.Tensor))  # should print: True
print(isinstance(y, torch.Tensor))

num_var = X.shape[1]

True
True


In [8]:
# setting test and training split (80:20)
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=0)

In [20]:
# Neural Network Model:

# including residual block / connections to skip some layers
class ResidualBlock(nn.Module):
    def __init__(self, in_features, out_features, activation, dropout_rate=0.1):
        super(ResidualBlock, self).__init__()
        self.linear1 = nn.Linear(in_features, out_features)
        self.activation1 = activation
        self.dropout1 = nn.Dropout(dropout_rate)
        self.linear2 = nn.Linear(out_features, out_features)
        self.activation2 = activation
        self.dropout2 = nn.Dropout(dropout_rate)
        self.shortcut = nn.Linear(in_features, out_features) if in_features != out_features else nn.Identity()
        self.batchnorm1 = nn.BatchNorm1d(out_features)
        self.batchnorm2 = nn.BatchNorm1d(out_features)
        
    def forward(self, x):
        identity = self.shortcut(x)
        out = self.linear1(x)
        out = self.activation1(out)
        out = self.batchnorm1(out)
        out = self.dropout1(out)
        out = self.linear2(out)
        out = self.activation2(out)
        out = self.batchnorm2(out)
        out = self.dropout2(out)
        out += identity
        return out

class MyModel(nn.Module):
    def __init__(self, num_layers, hidden_units, activations, dropout_rate):
        super(MyModel, self).__init__()
        layers = []
        in_features = X_train.shape[1]
        for i in range(num_layers):
            activation = nn.ReLU() if activations[i] == 'ReLU' else nn.Tanh() if activations[i] == 'Tanh' else nn.LeakyReLU()
            layers.append(ResidualBlock(in_features, hidden_units, activation, dropout_rate))
            in_features = hidden_units
        layers.append(nn.Linear(in_features, 1))
        self.model = nn.Sequential(*layers)

    def forward(self, x):
        return self.model(x)

def objective(trial):
    # hyperparameters being tuned with Optuna
    num_layers = trial.suggest_int('num_layers', 5, 30) 
    hidden_units = trial.suggest_categorical('hidden_units', [8, 16, 32, 64, 128, 256])
    activations = [trial.suggest_categorical(f'activation_{i}', ['ReLU', 'Tanh', 'LeakyReLU']) for i in range(num_layers)]
    lr = trial.suggest_loguniform('lr', 1e-3, 2e-2)
    n_epochs = trial.suggest_int('n_epochs', 1200, 1205)
    weight_decay = trial.suggest_loguniform('weight_decay', 1e-6, 1e-2)
    dropout_rate = trial.suggest_uniform('dropout_rate', 0.1, 0.5)
    
    # adaptive batch sizes
    initial_batch_size = trial.suggest_categorical('initial_batch_size', [128])
    final_batch_size = trial.suggest_categorical('final_batch_size', [256, 512, 1024])
    batch_size_ramp_epochs = trial.suggest_int('batch_size_ramp_epochs', 10, 50) # optuna suggests between given range how many epochs to move from initial batch size to final batch size
    
    # gradient accumulation steps
    accumulation_steps = 4  
    # future work should optimise this, set as flat figure to accelerate training
    
    # defining model now
    model = MyModel(num_layers, hidden_units, activations, dropout_rate)
    #loss_fn = nn.MSELoss() # MSE
    loss_fn = nn.L1Loss()  # MAE
    # Adam Optimiser
    optimiser = optim.Adam(model.parameters(), lr=lr, weight_decay=weight_decay)
    
    # calculating step_size_up across 7 epochs (adjusted for adaptive batch size)
    avg_batch_size = (initial_batch_size + final_batch_size) / 2
    num_batches_per_epoch = len(X_train) // avg_batch_size
    step_size_up = 7 * num_batches_per_epoch
    
    # setting cyclical learning rate scheduler
    scheduler = CyclicLR(optimiser, 
                         base_lr=lr / 10, # minimum learning rate
                         max_lr=lr,       # maximum learning rate
                         step_size_up=step_size_up,
                         mode='triangular2') # triangulates up and down but lr decreases each time (converges)
    
    # early stopping (if no improvement after 8 epochs)
    best_val_loss = float('inf')
    patience, trials_without_improvement = 8, 0
    
    # Training loop
    for epoch in range(n_epochs):
        model.train()
        
        # calculating current batch size
        if epoch < batch_size_ramp_epochs: # for batch size ramp up
            current_batch_size = int(initial_batch_size + (final_batch_size - initial_batch_size) * (epoch / batch_size_ramp_epochs))
        else:
            current_batch_size = final_batch_size # once at max batch size
        
        for i in range(0, len(X_train), current_batch_size):
            Xbatch = X_train[i:i+current_batch_size]
            ybatch = y_train[i:i+current_batch_size]
            y_pred = model(Xbatch) # predictions per batch
            loss = loss_fn(y_pred, ybatch) # loss of those predictions
            loss = loss / accumulation_steps  # normalising the loss (accomodates for gradient accumulation)
            loss.backward() # passing backwards to compute gradients 
            
            # uppdating model when gradients accumulated
            if ((i // current_batch_size) + 1) % accumulation_steps == 0:
                nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)  # gradient clipping (stops it getting too large)
                optimiser.step() # updating model based on new gradients
                model.zero_grad() # clearing gradients for next loop
                scheduler.step()  # updating the learning rate as per the scheduler
        
        # printing current learning rate after each epoch (helps monitor model behaviour)
        current_lr = optimiser.param_groups[0]['lr']
        print(f'Epoch {epoch+1}/{n_epochs}, Current learning rate: {current_lr}, Batch size: {current_batch_size}')
        
        # Calculating scores at each epoch
        model.eval() # setting to evaluation mode
        with torch.no_grad(): # no gradiaent calculations for validation
            y_train_pred = model(X_train) # predictions on entire training data
            train_loss = loss_fn(y_train_pred, y_train).item() # getting training loss
            # getting R2 score for training
            y_train_pred_np = y_train_pred.numpy().flatten()
            y_train_np = y_train.numpy().flatten()
            r2 = r2_score(y_train_np, y_train_pred_np)
            # printing training metrics
            print(f'Epoch {epoch+1}/{n_epochs}, Training Loss: {train_loss:.4f}, R2 Score: {r2:.4f}')
        
        # Validation
        with torch.no_grad(): # no gradiaent calculations for validation
            y_pred = model(X_val) # making predictions for validation data now
            val_loss = loss_fn(y_pred, y_val).item() # getting validation loss
            val_mse = mean_squared_error(y_val.numpy(), y_pred.numpy()) # getting MSE
            # getting R2 score for validation
            y_val_pred_np = y_pred.numpy().flatten()
            y_val_np = y_val.numpy().flatten()
            val_r2 = r2_score(y_val_np, y_val_pred_np)
        
        # checking for early stopping
        if val_loss < best_val_loss: # if validation loss is smaller then updating best_val_loss
            best_val_loss = val_loss
            trials_without_improvement = 0
        else:
            trials_without_improvement += 1
            if trials_without_improvement >= patience:
                print(f'Early stopping at epoch {epoch+1}')
                break
         # printing validation metrics       
        print(f'Epoch {epoch+1}/{n_epochs}, Validation Loss: {val_loss:.4f}, MSE: {val_mse:.4f}, R2 Score: {val_r2:.4f}')
        
        model.train() # setting model back to training mode for next loop
    
    return val_loss, val_r2

# initialising hyperparamter optimisation
study = optuna.create_study(direction='minimize',
                           pruner=MedianPruner(n_startup_trials=5, # number of trials before pruning starts
                                               n_warmup_steps=30, # number of steps before pruning can start
                                               interval_steps=10)) # how often pruning is considered
study.optimize(objective, 
               n_trials=1000, # setting for many trials so it does not stop prematurely
               timeout=777600 # units are seconds (here 9 days)
              )  

print('Number of finished trials: ', len(study.trials))
print('Best trial:')
trial = study.best_trial
print('  Value: ', trial.value)
print('  Params: ')
for key, value in trial.params.items():
    print('    {}: {}'.format(key, value))

[I 2024-07-14 10:46:06,039] A new study created in memory with name: no-name-825cdf4c-b5f1-4384-8fea-3739a8ccdf8f
C:\Users\lewil\AppData\Local\Temp\ipykernel_1388\1050023738.py:51: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  lr = trial.suggest_loguniform('lr', 1e-3, 2e-2)
C:\Users\lewil\AppData\Local\Temp\ipykernel_1388\1050023738.py:53: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  weight_decay = trial.suggest_loguniform('weight_decay', 1e-6, 1e-2)
C:\Users\lewil\AppData\Local\Temp\ipykernel_1388\1050023738.py:54: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.

Epoch 1/1205, Current learning rate: 0.001904015325506281, Batch size: 128
Epoch 1/1205, Training Loss: 276326.0312, R2 Score: -0.2607
Epoch 1/1205, Validation Loss: 272281.1562, MSE: 172653838336.0000, R2 Score: -1.0597
Epoch 2/1205, Current learning rate: 0.002507852543581266, Batch size: 131
Epoch 2/1205, Training Loss: 274204.7188, R2 Score: -0.2414
Epoch 2/1205, Validation Loss: 270234.0938, MSE: 166090276864.0000, R2 Score: -0.9814
Epoch 3/1205, Current learning rate: 0.003095640931939975, Batch size: 135
Epoch 3/1205, Training Loss: 270617.2500, R2 Score: -0.2238
Epoch 3/1205, Validation Loss: 266692.4375, MSE: 160102580224.0000, R2 Score: -0.9100
Epoch 4/1205, Current learning rate: 0.0036653743868678658, Batch size: 139
Epoch 4/1205, Training Loss: 275916.1562, R2 Score: -0.3135
Epoch 4/1205, Validation Loss: 271846.3438, MSE: 190908481536.0000, R2 Score: -1.2775
Epoch 5/1205, Current learning rate: 0.0042190590120794805, Batch size: 143
Epoch 5/1205, Training Loss: 252634.171

[W 2024-07-14 11:11:11,249] Trial 0 failed with parameters: {'num_layers': 28, 'hidden_units': 64, 'activation_0': 'Tanh', 'activation_1': 'LeakyReLU', 'activation_2': 'LeakyReLU', 'activation_3': 'LeakyReLU', 'activation_4': 'ReLU', 'activation_5': 'LeakyReLU', 'activation_6': 'ReLU', 'activation_7': 'LeakyReLU', 'activation_8': 'LeakyReLU', 'activation_9': 'LeakyReLU', 'activation_10': 'LeakyReLU', 'activation_11': 'LeakyReLU', 'activation_12': 'LeakyReLU', 'activation_13': 'Tanh', 'activation_14': 'ReLU', 'activation_15': 'LeakyReLU', 'activation_16': 'LeakyReLU', 'activation_17': 'Tanh', 'activation_18': 'ReLU', 'activation_19': 'Tanh', 'activation_20': 'ReLU', 'activation_21': 'ReLU', 'activation_22': 'Tanh', 'activation_23': 'Tanh', 'activation_24': 'LeakyReLU', 'activation_25': 'ReLU', 'activation_26': 'ReLU', 'activation_27': 'Tanh', 'lr': 0.012841292777150196, 'n_epochs': 1205, 'weight_decay': 8.656158600883416e-05, 'dropout_rate': 0.39966539842705073, 'initial_batch_size': 12

Epoch 1/1200, Current learning rate: 0.00015086251368248206, Batch size: 128
Epoch 1/1200, Training Loss: 277718.5312, R2 Score: -0.2527
Epoch 1/1200, Validation Loss: 273724.7188, MSE: 169875046400.0000, R2 Score: -1.0266
Epoch 2/1200, Current learning rate: 0.00019870687677846013, Batch size: 131
Epoch 2/1200, Training Loss: 277856.1562, R2 Score: -0.2454
Epoch 2/1200, Validation Loss: 273888.4062, MSE: 167355105280.0000, R2 Score: -0.9965
Epoch 3/1200, Current learning rate: 0.00024527962889514326, Batch size: 135
Epoch 3/1200, Training Loss: 277655.1250, R2 Score: -0.2546
Epoch 3/1200, Validation Loss: 273651.0312, MSE: 170540826624.0000, R2 Score: -1.0345
Epoch 4/1200, Current learning rate: 0.00029073972140494314, Batch size: 138
Epoch 4/1200, Training Loss: 277608.0312, R2 Score: -0.2511
Epoch 4/1200, Validation Loss: 273620.1562, MSE: 169342353408.0000, R2 Score: -1.0202
Epoch 5/1200, Current learning rate: 0.00033492820293544765, Batch size: 142
Epoch 5/1200, Training Loss: 27

[W 2024-07-14 11:46:45,600] Trial 1 failed with parameters: {'num_layers': 28, 'hidden_units': 8, 'activation_0': 'ReLU', 'activation_1': 'LeakyReLU', 'activation_2': 'ReLU', 'activation_3': 'Tanh', 'activation_4': 'ReLU', 'activation_5': 'ReLU', 'activation_6': 'Tanh', 'activation_7': 'ReLU', 'activation_8': 'Tanh', 'activation_9': 'LeakyReLU', 'activation_10': 'LeakyReLU', 'activation_11': 'Tanh', 'activation_12': 'LeakyReLU', 'activation_13': 'LeakyReLU', 'activation_14': 'Tanh', 'activation_15': 'LeakyReLU', 'activation_16': 'ReLU', 'activation_17': 'Tanh', 'activation_18': 'ReLU', 'activation_19': 'ReLU', 'activation_20': 'LeakyReLU', 'activation_21': 'ReLU', 'activation_22': 'LeakyReLU', 'activation_23': 'LeakyReLU', 'activation_24': 'LeakyReLU', 'activation_25': 'LeakyReLU', 'activation_26': 'Tanh', 'activation_27': 'ReLU', 'lr': 0.001017465396072091, 'n_epochs': 1200, 'weight_decay': 0.009454000419425181, 'dropout_rate': 0.1847226797262887, 'initial_batch_size': 128, 'final_bat

...

Epoch 1/1203, Current learning rate: 0.0004621797687340026, Batch size: 128
Epoch 1/1203, Training Loss: 277672.8750, R2 Score: -0.2571
Epoch 1/1203, Validation Loss: 273657.0938, MSE: 171380965376.0000, R2 Score: -1.0445
Epoch 2/1203, Current learning rate: 0.0006102158079819811, Batch size: 130
Epoch 2/1203, Training Loss: 277516.0938, R2 Score: -0.2541
Epoch 2/1203, Validation Loss: 273513.1875, MSE: 170356523008.0000, R2 Score: -1.0323
Epoch 3/1203, Current learning rate: 0.0007548431226420138, Batch size: 133
Epoch 3/1203, Training Loss: 277363.0625, R2 Score: -0.2553
Epoch 3/1203, Validation Loss: 273353.2188, MSE: 170766974976.0000, R2 Score: -1.0372
Epoch 4/1203, Current learning rate: 0.0008975225946803608, Batch size: 135
Epoch 4/1203, Training Loss: 277358.8750, R2 Score: -0.2625
Epoch 4/1203, Validation Loss: 273313.5938, MSE: 173269303296.0000, R2 Score: -1.0671
Epoch 5/1203, Current learning rate: 0.0010367933421307621, Batch size: 138
Epoch 5/1203, Training Loss: 277153.

[W 2024-07-14 18:20:58,526] Trial 5 failed with parameters: {'num_layers': 21, 'hidden_units': 8, 'activation_0': 'LeakyReLU', 'activation_1': 'Tanh', 'activation_2': 'LeakyReLU', 'activation_3': 'LeakyReLU', 'activation_4': 'ReLU', 'activation_5': 'LeakyReLU', 'activation_6': 'Tanh', 'activation_7': 'ReLU', 'activation_8': 'Tanh', 'activation_9': 'LeakyReLU', 'activation_10': 'LeakyReLU', 'activation_11': 'ReLU', 'activation_12': 'LeakyReLU', 'activation_13': 'Tanh', 'activation_14': 'LeakyReLU', 'activation_15': 'Tanh', 'activation_16': 'LeakyReLU', 'activation_17': 'ReLU', 'activation_18': 'Tanh', 'activation_19': 'Tanh', 'activation_20': 'LeakyReLU', 'lr': 0.003117089262089197, 'n_epochs': 1203, 'weight_decay': 0.0001289000890213348, 'dropout_rate': 0.2637266068826868, 'initial_batch_size': 128, 'final_batch_size': 256, 'batch_size_ramp_epochs': 49} because of the following error: The number of the values 2 did not match the number of the objectives 1.
[W 2024-07-14 18:20:58,526] T

Epoch 1/1205, Current learning rate: 0.0001605386234574822, Batch size: 128
Epoch 1/1205, Training Loss: 277553.7812, R2 Score: -0.2494
Epoch 1/1205, Validation Loss: 273571.6875, MSE: 168749334528.0000, R2 Score: -1.0131
Epoch 2/1205, Current learning rate: 0.00021195909568642995, Batch size: 130
Epoch 2/1205, Training Loss: 277458.9062, R2 Score: -0.2564
Epoch 2/1205, Validation Loss: 273443.8125, MSE: 171171446784.0000, R2 Score: -1.0420
Epoch 3/1205, Current learning rate: 0.00026219554388379044, Batch size: 133
Epoch 3/1205, Training Loss: 277375.3438, R2 Score: -0.2471
Epoch 3/1205, Validation Loss: 273400.5312, MSE: 167954104320.0000, R2 Score: -1.0037
Epoch 4/1205, Current learning rate: 0.0003112479680495628, Batch size: 136
Epoch 4/1205, Training Loss: 277246.0000, R2 Score: -0.2454
Epoch 4/1205, Validation Loss: 273276.1250, MSE: 167366590464.0000, R2 Score: -0.9966
Epoch 5/1205, Current learning rate: 0.00035928551447397437, Batch size: 139
Epoch 5/1205, Training Loss: 2770

[W 2024-07-14 18:45:31,690] Trial 6 failed with parameters: {'num_layers': 27, 'hidden_units': 32, 'activation_0': 'LeakyReLU', 'activation_1': 'ReLU', 'activation_2': 'Tanh', 'activation_3': 'LeakyReLU', 'activation_4': 'LeakyReLU', 'activation_5': 'Tanh', 'activation_6': 'Tanh', 'activation_7': 'LeakyReLU', 'activation_8': 'LeakyReLU', 'activation_9': 'ReLU', 'activation_10': 'Tanh', 'activation_11': 'ReLU', 'activation_12': 'ReLU', 'activation_13': 'Tanh', 'activation_14': 'Tanh', 'activation_15': 'ReLU', 'activation_16': 'Tanh', 'activation_17': 'LeakyReLU', 'activation_18': 'ReLU', 'activation_19': 'LeakyReLU', 'activation_20': 'ReLU', 'activation_21': 'Tanh', 'activation_22': 'ReLU', 'activation_23': 'Tanh', 'activation_24': 'ReLU', 'activation_25': 'LeakyReLU', 'activation_26': 'LeakyReLU', 'lr': 0.0010827241977740061, 'n_epochs': 1205, 'weight_decay': 2.7206809420705534e-06, 'dropout_rate': 0.17760690910654683, 'initial_batch_size': 128, 'final_batch_size': 256, 'batch_size_ram

ValueError: Expected more than 1 value per channel when training, got input size torch.Size([1, 32])

In [ ]:
# saving results to .txt file
filename = "NN_results.txt"

with open(filename, 'w') as f:
    f.write("Neural Network Hyperparamter Tuning Results\n")
    f.write("=========================================\n\n")
    f.write(f"Number of finished trials: {len(study.trials)}\n\n")
    f.write("Best trial:\n")
    trial = study.best_trial
    f.write(f"  Value (MSE): {trial.value}\n")
    f.write(f"  R2 Score: {trial.values[1]}\n")
    f.write("  Params:\n")
    for key, value in trial.params.items():
        f.write(f"    {key}: {value}\n")
    
    f.write("\nAll trials:\n")
    for i, trial in enumerate(study.trials):
        f.write(f"\nTrial {i+1}:\n")
        f.write(f"  Value (MSE): {trial.value}\n")
        f.write(f"  R2 Score: {trial.values[1]}\n")
        f.write("  Params:\n")
        for key, value in trial.params.items():
            f.write(f"    {key}: {value}\n")

print(f"\nResults saved to {filename}")

In [30]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.optim.lr_scheduler import CyclicLR
from torch.utils.data import DataLoader, TensorDataset
from sklearn.metrics import r2_score, mean_squared_error
import optuna
from optuna.pruners import MedianPruner

# Define the ResidualBlock class with conditional BatchNorm1d
class ResidualBlock(nn.Module):
    def __init__(self, in_features, out_features, activation, dropout_rate=0.1):
        super(ResidualBlock, self).__init__()
        self.linear1 = nn.Linear(in_features, out_features)
        self.activation1 = activation
        self.dropout1 = nn.Dropout(dropout_rate)
        self.linear2 = nn.Linear(out_features, out_features)
        self.activation2 = activation
        self.dropout2 = nn.Dropout(dropout_rate)
        self.shortcut = nn.Linear(in_features, out_features) if in_features != out_features else nn.Identity()
        self.batchnorm1 = nn.BatchNorm1d(out_features)
        self.batchnorm2 = nn.BatchNorm1d(out_features)
       
    def forward(self, x):
        identity = self.shortcut(x)
        out = self.linear1(x)
        out = self.activation1(out)
        if out.size(0) > 1:  # Apply batchnorm only if batch size > 1
            out = self.batchnorm1(out)
        out = self.dropout1(out)
        out = self.linear2(out)
        out = self.activation2(out)
        if out.size(0) > 1:  # Apply batchnorm only if batch size > 1
            out = self.batchnorm2(out)
        out = self.dropout2(out)
        out += identity
        return out

# Define the MyModel class
class MyModel(nn.Module):
    def __init__(self, num_layers, hidden_units, activations, dropout_rate):
        super(MyModel, self).__init__()
        layers = []
        in_features = X_train.shape[1]
        for i in range(num_layers):
            activation = nn.ReLU() if activations[i] == 'ReLU' else nn.Tanh() if activations[i] == 'Tanh' else nn.LeakyReLU()
            layers.append(ResidualBlock(in_features, hidden_units, activation, dropout_rate))
            in_features = hidden_units
        layers.append(nn.Linear(in_features, 1))
        self.model = nn.Sequential(*layers)

    def forward(self, x):
        return self.model(x)

# Define the objective function
def objective(trial):
    # Suggest hyperparameters
    num_layers = trial.suggest_int('num_layers', 5, 30)
    hidden_units = trial.suggest_categorical('hidden_units', [8, 16, 32, 64, 128, 256])
    activations = [trial.suggest_categorical(f'activation_{i}', ['ReLU', 'Tanh', 'LeakyReLU']) for i in range(num_layers)]
    lr = trial.suggest_loguniform('lr', 1e-3, 2e-2)
    n_epochs = trial.suggest_int('n_epochs', 1200, 1205)
    weight_decay = trial.suggest_loguniform('weight_decay', 1e-6, 1e-2)
    dropout_rate = trial.suggest_uniform('dropout_rate', 0.1, 0.5)
   
    # Adaptive batch size parameters
    initial_batch_size = trial.suggest_categorical('initial_batch_size', [128])
    final_batch_size = trial.suggest_categorical('final_batch_size', [256, 512, 1024])
    batch_size_ramp_epochs = trial.suggest_int('batch_size_ramp_epochs', 10, 50)
   
    # Gradient accumulation steps
    accumulation_steps = 4
   
    # Define model
    model = MyModel(num_layers, hidden_units, activations, dropout_rate)
    loss_fn = nn.L1Loss()  # MAE
    optimiser = optim.Adam(model.parameters(), lr=lr, weight_decay=weight_decay)
   
    # Calculate step_size_up for 7 epochs (adjusted for adaptive batch size)
    avg_batch_size = (initial_batch_size + final_batch_size) / 2
    num_batches_per_epoch = len(X_train) // avg_batch_size
    step_size_up = 7 * num_batches_per_epoch
   
    # Define the cyclical learning rate scheduler
    scheduler = CyclicLR(optimiser,
                         base_lr=lr / 10,
                         max_lr=lr,
                         step_size_up=step_size_up,
                         mode='triangular2')
   
    # Early stopping
    best_val_loss = float('inf')
    patience, trials_without_improvement = 8, 0
   
    # Create TensorDataset and DataLoader
    train_dataset = TensorDataset(X_train, y_train)
    val_dataset = TensorDataset(X_val, y_val)
   
    # Training loop
    for epoch in range(n_epochs):
        model.train()
       
        # Calculate current batch size
        if epoch < batch_size_ramp_epochs:
            current_batch_size = int(initial_batch_size + (final_batch_size - initial_batch_size) * (epoch / batch_size_ramp_epochs))
        else:
            current_batch_size = final_batch_size
       
        train_loader = DataLoader(train_dataset, batch_size=current_batch_size, shuffle=True)
       
        for batch_idx, (Xbatch, ybatch) in enumerate(train_loader):
            y_pred = model(Xbatch)
            loss = loss_fn(y_pred, ybatch)
            loss = loss / accumulation_steps  # Normalize the loss
            loss.backward()
           
            if (batch_idx + 1) % accumulation_steps == 0:
                nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)  # Gradient clipping
                optimiser.step()
                model.zero_grad()
                scheduler.step()  # Update the learning rate
       
        # Print current learning rate at the end of each epoch
        current_lr = optimiser.param_groups[0]['lr']
        print(f'Epoch {epoch+1}/{n_epochs}, Current learning rate: {current_lr}, Batch size: {current_batch_size}')
       
        # Calculating scores at each epoch
        model.eval()
        with torch.no_grad():
            # Training loss (MSE)
            y_train_pred = model(X_train)
            train_loss = loss_fn(y_train_pred, y_train).item()
            # R2 score
            y_train_pred_np = y_train_pred.numpy().flatten()
            y_train_np = y_train.numpy().flatten()
            r2 = r2_score(y_train_np, y_train_pred_np)
            # printing training metrics
            print(f'Epoch {epoch+1}/{n_epochs}, Training Loss: {train_loss:.4f}, R2 Score: {r2:.4f}')
       
        # Validation
        with torch.no_grad():
            y_pred = model(X_val)
            val_loss = loss_fn(y_pred, y_val).item()
            val_mse = mean_squared_error(y_val.numpy(), y_pred.numpy())
            y_val_pred_np = y_pred.numpy().flatten()
            y_val_np = y_val.numpy().flatten()
            val_r2 = r2_score(y_val_np, y_val_pred_np)
       
        # Check for early stopping
        if val_loss < best_val_loss:
            best_val_loss = val_loss
            trials_without_improvement = 0
        else:
            trials_without_improvement += 1
            if trials_without_improvement >= patience:
                print(f'Early stopping at epoch {epoch+1}')
                break
         # printing validation metrics      
        print(f'Epoch {epoch+1}/{n_epochs}, Validation Loss: {val_loss:.4f}, MSE: {val_mse:.4f}, R2 Score: {val_r2:.4f}')
       
        # Setting model back to training mode
        model.train()
   
    return val_loss, val_r2

# Optuna study
study = optuna.create_study(direction='minimize',
                           pruner=MedianPruner(n_startup_trials=5,
                                               n_warmup_steps=30,
                                               interval_steps=10))
study.optimize(objective,
               n_trials=1000,
               timeout=777600 # units are seconds (here 9 days)
              )  

print('Number of finished trials: ', len(study.trials))
print('Best trial MSE:')
trial = study.best_trial
print('  Value: ', trial.value)
print('  Params: ')
for key, value in trial.params.items():
    print('    {}: {}'.format(key, value))


[I 2024-07-14 22:53:56,490] A new study created in memory with name: no-name-4c4d0b11-60c3-4592-b704-a44f95eb1f8d
C:\Users\lewil\AppData\Local\Temp\ipykernel_1388\429490832.py:61: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  lr = trial.suggest_loguniform('lr', 1e-3, 2e-2)
C:\Users\lewil\AppData\Local\Temp\ipykernel_1388\429490832.py:63: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  weight_decay = trial.suggest_loguniform('weight_decay', 1e-6, 1e-2)
C:\Users\lewil\AppData\Local\Temp\ipykernel_1388\429490832.py:64: FutureWarning: suggest_uniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0

Epoch 1/1204, Current learning rate: 0.0005909168003219722, Batch size: 128
Epoch 1/1204, Training Loss: 277668.7812, R2 Score: -0.2562
Epoch 1/1204, Validation Loss: 273657.0938, MSE: 171077697536.0000, R2 Score: -1.0409
Epoch 2/1204, Current learning rate: 0.0007801872716028102, Batch size: 130
Epoch 2/1204, Training Loss: 277452.5625, R2 Score: -0.2562
Epoch 2/1204, Validation Loss: 273439.0938, MSE: 171089739776.0000, R2 Score: -1.0411
Epoch 3/1204, Current learning rate: 0.0009650995412423143, Batch size: 133
Epoch 3/1204, Training Loss: 277824.4375, R2 Score: -0.2347
Epoch 3/1204, Validation Loss: 273874.7812, MSE: 163657564160.0000, R2 Score: -0.9524
Epoch 4/1204, Current learning rate: 0.0011456536092404814, Batch size: 136
Epoch 4/1204, Training Loss: 276678.5938, R2 Score: -0.2513
Epoch 4/1204, Validation Loss: 272681.7188, MSE: 169420800000.0000, R2 Score: -1.0212
Epoch 5/1204, Current learning rate: 0.0013237172763007439, Batch size: 138
Epoch 5/1204, Training Loss: 275969.

[W 2024-07-14 23:06:14,360] Trial 0 failed with parameters: {'num_layers': 5, 'hidden_units': 16, 'activation_0': 'Tanh', 'activation_1': 'LeakyReLU', 'activation_2': 'ReLU', 'activation_3': 'Tanh', 'activation_4': 'LeakyReLU', 'lr': 0.003985333278687528, 'n_epochs': 1204, 'weight_decay': 5.732939878465895e-06, 'dropout_rate': 0.3231270254474998, 'initial_batch_size': 128, 'final_batch_size': 256, 'batch_size_ramp_epochs': 47} because of the following error: The number of the values 2 did not match the number of the objectives 1.
[W 2024-07-14 23:06:14,361] Trial 0 failed with value (160615.71875, -0.03954919980724125).
C:\Users\lewil\AppData\Local\Temp\ipykernel_1388\429490832.py:61: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use suggest_float(..., log=True) instead.
  lr = trial.suggest_loguniform('lr', 1e-3, 2e-2)
C:\Users\lewil\AppData\Local\Temp\ipykernel_1388\42

Epoch 1/1201, Current learning rate: 0.00027424839425514854, Batch size: 128
Epoch 1/1201, Training Loss: 11459776.0000, R2 Score: -58987369.5282
Epoch 1/1201, Validation Loss: 273596.6562, MSE: 168874459136.0000, R2 Score: -1.0146
Epoch 2/1201, Current learning rate: 0.0003892821429414433, Batch size: 180
Epoch 2/1201, Training Loss: 277467.6562, R2 Score: -0.2474
Epoch 2/1201, Validation Loss: 273492.8125, MSE: 168072347648.0000, R2 Score: -1.0051
Epoch 3/1201, Current learning rate: 0.00047805247868566123, Batch size: 233
Epoch 3/1201, Training Loss: 277821.9688, R2 Score: -0.2702
Epoch 3/1201, Validation Loss: 273748.3438, MSE: 175889268736.0000, R2 Score: -1.0983
Epoch 4/1201, Current learning rate: 0.0005505394984057921, Batch size: 286
Epoch 4/1201, Training Loss: 277604.2812, R2 Score: -0.2400
Epoch 4/1201, Validation Loss: 273646.2500, MSE: 165499158528.0000, R2 Score: -0.9744
Epoch 5/1201, Current learning rate: 0.0006119958846902508, Batch size: 338
Epoch 5/1201, Training Lo

[W 2024-07-15 03:02:29,334] Trial 1 failed with parameters: {'num_layers': 19, 'hidden_units': 16, 'activation_0': 'ReLU', 'activation_1': 'LeakyReLU', 'activation_2': 'Tanh', 'activation_3': 'LeakyReLU', 'activation_4': 'LeakyReLU', 'activation_5': 'ReLU', 'activation_6': 'Tanh', 'activation_7': 'LeakyReLU', 'activation_8': 'LeakyReLU', 'activation_9': 'ReLU', 'activation_10': 'LeakyReLU', 'activation_11': 'LeakyReLU', 'activation_12': 'Tanh', 'activation_13': 'ReLU', 'activation_14': 'Tanh', 'activation_15': 'Tanh', 'activation_16': 'ReLU', 'activation_17': 'LeakyReLU', 'activation_18': 'ReLU', 'lr': 0.0011194050227311665, 'n_epochs': 1201, 'weight_decay': 3.995894079670607e-05, 'dropout_rate': 0.4048855004449675, 'initial_batch_size': 128, 'final_batch_size': 1024, 'batch_size_ramp_epochs': 17} because of the following error: The number of the values 2 did not match the number of the objectives 1.
[W 2024-07-15 03:02:29,336] Trial 1 failed with value (160593.15625, 0.034295496126130

...

[W 2024-07-23 19:19:04,541] Trial 88 failed with parameters: {'num_layers': 28, 'hidden_units': 64, 'activation_0': 'ReLU', 'activation_1': 'Tanh', 'activation_2': 'ReLU', 'activation_3': 'LeakyReLU', 'activation_4': 'Tanh', 'activation_5': 'Tanh', 'activation_6': 'ReLU', 'activation_7': 'LeakyReLU', 'activation_8': 'LeakyReLU', 'activation_9': 'Tanh', 'activation_10': 'LeakyReLU', 'activation_11': 'LeakyReLU', 'activation_12': 'Tanh', 'activation_13': 'ReLU', 'activation_14': 'Tanh', 'activation_15': 'Tanh', 'activation_16': 'Tanh', 'activation_17': 'LeakyReLU', 'activation_18': 'LeakyReLU', 'activation_19': 'LeakyReLU', 'activation_20': 'ReLU', 'activation_21': 'ReLU', 'activation_22': 'Tanh', 'activation_23': 'Tanh', 'activation_24': 'LeakyReLU', 'activation_25': 'LeakyReLU', 'activation_26': 'ReLU', 'activation_27': 'Tanh', 'lr': 0.005242486363196938, 'n_epochs': 1200, 'weight_decay': 4.048736830763295e-05, 'dropout_rate': 0.15339176210395405, 'initial_batch_size': 128, 'final_batc

Epoch 1/1201, Current learning rate: 0.00024097817107390242, Batch size: 128
Epoch 1/1201, Training Loss: 57336807424.0000, R2 Score: -1550842396541179.7500
Epoch 1/1201, Validation Loss: 275955.6562, MSE: 161582579712.0000, R2 Score: -0.9276
Epoch 2/1201, Current learning rate: 0.0003181634059203316, Batch size: 130
Epoch 2/1201, Training Loss: 278509.5938, R2 Score: -0.2363
Epoch 2/1201, Validation Loss: 274505.8438, MSE: 163707781120.0000, R2 Score: -0.9530
Epoch 3/1201, Current learning rate: 0.00039357134917490265, Batch size: 133
Epoch 3/1201, Training Loss: 280216.3125, R2 Score: -0.3020
Epoch 3/1201, Validation Loss: 276110.9375, MSE: 186737688576.0000, R2 Score: -1.2277
Epoch 4/1201, Current learning rate: 0.0004679636972341252, Batch size: 135
Epoch 4/1201, Training Loss: 277111.0938, R2 Score: -0.2538
Epoch 4/1201, Validation Loss: 273105.9375, MSE: 170287120384.0000, R2 Score: -1.0315
Epoch 5/1201, Current learning rate: 0.0005405787537014897, Batch size: 138
Epoch 5/1201, 

[W 2024-07-24 01:43:33,743] Trial 89 failed with parameters: {'num_layers': 26, 'hidden_units': 128, 'activation_0': 'ReLU', 'activation_1': 'ReLU', 'activation_2': 'Tanh', 'activation_3': 'ReLU', 'activation_4': 'LeakyReLU', 'activation_5': 'LeakyReLU', 'activation_6': 'Tanh', 'activation_7': 'ReLU', 'activation_8': 'LeakyReLU', 'activation_9': 'ReLU', 'activation_10': 'ReLU', 'activation_11': 'ReLU', 'activation_12': 'ReLU', 'activation_13': 'Tanh', 'activation_14': 'Tanh', 'activation_15': 'LeakyReLU', 'activation_16': 'Tanh', 'activation_17': 'LeakyReLU', 'activation_18': 'LeakyReLU', 'activation_19': 'LeakyReLU', 'activation_20': 'Tanh', 'activation_21': 'LeakyReLU', 'activation_22': 'Tanh', 'activation_23': 'LeakyReLU', 'activation_24': 'LeakyReLU', 'activation_25': 'ReLU', 'lr': 0.0016252344223328886, 'n_epochs': 1201, 'weight_decay': 0.00217783779937323, 'dropout_rate': 0.41896967060083434, 'initial_batch_size': 128, 'final_batch_size': 256, 'batch_size_ramp_epochs': 50} becaus

Number of finished trials:  90
Best trial MSE:


ValueError: No trials are completed yet.